In [3]:
import numpy as np
import plotly
import plotly.offline as py
import plotly.graph_objs as go
from plotly import tools
plotly.offline.init_notebook_mode()
np.set_printoptions(precision=4, suppress=True)

In [4]:
def gen_rand_matrix(n):
    A = np.random.uniform(-1, 1, size=(n, n))
    return A @ A.T

In [5]:
def gen_hilbert_matrix(n):
    return np.array([[1.0 / (i + j + 1) for j in range(n)] 
                     for i in range(n)])

In [6]:
def gen_conditional_matrix(n, noise=0.1):
    A = np.eye(n) + np.random.normal(scale=noise, size=(n, n))
    return A @ A.T

In [7]:
def calc_cond(A):
    A_inv = np.linalg.inv(A)
    return np.linalg.norm(A) * np.linalg.norm(A_inv)

In [8]:
def gen_unconditional_matrix(n, iters=5*10**4):
    best_matrix = None
    best_cond = None
    for it in range(iters):
        A = np.random.binomial(30, 0.1, size=(n, n)) - 15
        A = A @ A.T
        cond = calc_cond(A)
        if best_matrix is None or cond > best_cond:
            best_cond, best_matrix = cond, A 
    return best_matrix

In [9]:
def test_conditions(A, b):
    A = np.array(A, dtype='float32')
    b = np.array(b, dtype='float32')
    assert len(A.shape) == 2
    assert A.shape[0] == A.shape[1]
    assert len(b.shape) == 1
    assert b.shape[0] == A.shape[0]
    return A, b

In [10]:
def solve_gauss(A, b, eps=1e-9):
    A, b = test_conditions(A, b)
    n = A.shape[0]
    A = np.concatenate((A, b.reshape((-1, 1))), axis=1)
    for i in range(n):
        column_i = A.T[i]
        ind = np.argmax(np.abs(column_i[i:])) + i
        
        v = A[ind][i]
        if np.abs(v) < eps:
            return None
        
        A[ind], A[i] = A[i], A[ind] / v
        
        for j in range(n):
            if j == i:
                continue
            c = A[j][i]
            A[j] -= A[i] * c
    return A.T[n]

In [11]:
def solve_conjugate_gradient(A, b, eps=1e-6, max_iter=10**3, history=None):
    A, b = test_conditions(A, b)
    assert np.linalg.norm(A - A.T) < eps
    n = A.shape[0]
    
    xk = np.random.normal(size=n)
    rk = b - A @ xk
    zk = rk
    r2k = np.dot(rk, rk)
    
    for k in range(max_iter):
        t = np.linalg.norm(A @ xk - b)
        if history is not None:
            history.append(t)
        if t < eps:
            break
        a = r2k / np.dot(A @ zk, zk)
        x_next = xk + a * zk
        r_next = rk - a * A @ zk
        r2_next = np.dot(r_next, r_next)
        z_next = r_next + zk * r2_next / r2k
        xk, rk, zk, r2k = x_next, r_next, z_next, r2_next
    return xk

In [12]:
def solve_jacobi(A, b, eps=1e-6, max_iter=10**3, history=None):
    A, b = test_conditions(A, b)
    n = A.shape[0]
    
    D = np.diag(np.diag(A))
    D_inv = np.diag(1.0 / np.diag(A))
    R = A - D
    
    xk = np.random.normal(size=n)
    for k in range(max_iter):
        t = np.linalg.norm(A @ xk - b)
        if history is not None:
            history.append(t)
        if t < eps:
            break
        xk = D_inv @ (b - R @ xk)
    return xk

In [13]:
def solve_seidel(A, b, eps=1e-6, max_iter=10**3, history=None, relax=1):
    A, b = test_conditions(A, b)
    n = A.shape[0]
    
    xk = np.random.normal(size=n)
    for k in range(max_iter):
        t = np.linalg.norm(A @ xk - b)
        if history is not None:
            history.append(t)
        if t < eps:
            break
        for i in range(n):
            t = b[i] - np.dot(A[i][:i], xk[:i]) - np.dot(A[i][i+1:], xk[i+1:])
            t /= A[i][i]
            xk[i] = (1 - relax) * xk[i] + relax * t
    return xk

In [14]:
def solve_seidel_relax(A, b, eps=1e-6, max_iter=10**3, history=None, relax=0.9):
    return solve_seidel(A, b, eps, max_iter, history, relax)

In [15]:
def find_good_matrix():
    while True:
        n = 5
        Q = gen_rand_matrix(n)
        b = np.random.random(size=n)
        X = solve_seidel_relax(Q, b)
        Y = Q @ np.array(X)
        display(np.linalg.norm(Y - b))
        if np.linalg.norm(Y - b) < 1e-5:
            return Q, b

In [16]:
methods = [
    solve_gauss,
    solve_conjugate_gradient,
    solve_jacobi,
    solve_seidel,
    solve_seidel_relax
]
matrix_generators = [
    gen_rand_matrix,
    gen_hilbert_matrix,
    gen_conditional_matrix,
    gen_unconditional_matrix
]
N = 10

In [17]:
for matrix_g in matrix_generators:
    A = matrix_g(N)
    name = matrix_g.__name__
    cond = calc_cond(A)
    print(f'Matrix generated by {name} has cond = {cond}')

Matrix generated by gen_rand_matrix has cond = 19011.274541021165
Matrix generated by gen_hilbert_matrix has cond = 16333640022240.15
Matrix generated by gen_conditional_matrix has cond = 15.450962276476412
Matrix generated by gen_unconditional_matrix has cond = 1.7145374482976566e+17


In [18]:
data = {}
for matrix_g in matrix_generators:
    A = matrix_g(N)
    b = np.random.random(size=N)
    cur_data = data[matrix_g.__name__] = {}
    for method in methods:
        x = method(A, b)
        y = A @ x
        cur_data[method.__name__] = np.linalg.norm(y - b)

/home/josdas/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:16: RuntimeWarning:

overflow encountered in matmul

/home/josdas/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:16: RuntimeWarning:

invalid value encountered in matmul

/home/josdas/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:11: RuntimeWarning:

overflow encountered in matmul



In [19]:
import pandas as pd
pd.options.display.float_format = "{:,.5f}".format

In [20]:
pd.DataFrame(data=data)

gen_rand_matrix   gen_hilbert_matrix  \
solve_conjugate_gradient          0.00000 20,942,006,699.64814   
solve_gauss                       0.00001            274.09669   
solve_jacobi                          inf                  nan   
solve_seidel                      0.00000              0.76183   
solve_seidel_relax                0.00000              0.74030   

                          gen_conditional_matrix  gen_unconditional_matrix  
solve_conjugate_gradient                 0.00000             423,444.37751  
solve_gauss                              0.00000                 137.24220  
solve_jacobi                             0.00000                       nan  
solve_seidel                             0.00000                   2.50606  
solve_seidel_relax                       0.00000                  10.66022

In [21]:
A_GOOD = np.array(
    [[-0.8668, -0.4829,  0.4685,  0.2215,  0.4423],
    [ 0.6264,  0.722 ,  0.9024,  0.0049,  0.3023],
    [ 0.2448,  0.5063, -0.6736, -0.116 ,  0.1297],
    [-0.7807,  0.0771, -0.4845,  0.7591,  0.3819],
    [-0.6693, -0.9893,  0.1781,  0.0586, -0.8794]])
b_GOOD = [0.8773, 0.5407, 0.8606, 0.3697, 0.0802]

def test_method(method, symmetry=False):
    A, b = A_GOOD, b_GOOD
    if symmetry:
        A = A @ A.T
    history = []
    x = method(A, b, history=history)
    y = A @ x
    print(f'Method name: {method.__name__}')
    print(f'symmetry = {symmetry}')
    print(f'cond(A) = {calc_cond(A)}')
    print(f'Norm of delat = {np.linalg.norm(y - b)}')
    print(f'b = {b}')
    print(f'Ax = {y}')
    
    data = [go.Scatter(y=history)]
    layout = go.Layout(
        xaxis=go.layout.XAxis(title='iteration'),
        yaxis=go.layout.YAxis(title='norm(Ax - b)'),
        title=method.__name__,
        height=400,
    )
    fig = go.Figure(data=data, layout=layout)
    py.offline.iplot(fig)

In [23]:
methods_with_history_and_symmetry = [
    (solve_jacobi, False),
    (solve_jacobi, True),
    (solve_seidel, True),
    (solve_seidel_relax, True)
]
for method, symmetry in methods_with_history_and_symmetry:
    test_method(method, symmetry=symmetry)
    print('\n')

Method name: solve_jacobi
symmetry = False
cond(A) = 21.727409388522865
Norm of delat = 8.604169374092787e-07
b = [0.8773, 0.5407, 0.8606, 0.3697, 0.0802]
Ax = [0.8773 0.5407 0.8606 0.3697 0.0802]




Method name: solve_jacobi
symmetry = True
cond(A) = 260.0327590184174
Norm of delat = inf
b = [0.8773, 0.5407, 0.8606, 0.3697, 0.0802]
Ax = [-1.9231e+161  1.5252e+161  1.2731e+161 -1.0251e+161 -2.4449e+161]




Method name: solve_seidel
symmetry = True
cond(A) = 260.0327590184174
Norm of delat = 2.199704339692507e-06
b = [0.8773, 0.5407, 0.8606, 0.3697, 0.0802]
Ax = [0.8773 0.5407 0.8606 0.3697 0.0802]




Method name: solve_seidel_relax
symmetry = True
cond(A) = 260.0327590184174
Norm of delat = 2.0934931525601616e-06
b = [0.8773, 0.5407, 0.8606, 0.3697, 0.0802]
Ax = [0.8773 0.5407 0.8606 0.3697 0.0802]


In [28]:
from matplotlib import cm
COLOR_MAP = cm.get_cmap('plasma')

def get_color(v):
    r, g, b, _ = COLOR_MAP(v / 2)
    return 'rgb({},{},{})'.format(r, g, b)

In [29]:
def test_relaxation(parameters=None, log10=False):
    if parameters is None:
        parameters = np.linspace(0, 2, num=20)
    A, b = A_GOOD, b_GOOD
    A = A @ A.T
    results = {}
    for relax in parameters:
        history = []
        x = solve_seidel_relax(A, b, history=history, relax=relax)
        if log10:
            history = np.log10(history)
        results[relax] = history
        
    data = [go.Scatter(name=str(r), 
                       y=history,
                       line = dict(color=get_color(r)))
            for r, history in results.items()]
    if log10:
        title_y = 'log10(norm(Ax - b))'
        range_y = [-6, 1]
    else:
        title_y = 'norm(Ax - b)'
        range_y = [0, 1]
    layout = go.Layout(
        xaxis=go.layout.XAxis(
            title='iteration'
        ),
        yaxis=go.layout.YAxis(
            title=title_y, 
            range=range_y
        ),
        title='Seidel with relaxation',
        height=600,
    )
    fig = go.Figure(data=data, layout=layout)
    py.offline.iplot(fig)

In [30]:
test_relaxation()

In [31]:
test_relaxation(log10=True)